<h1 style="text-align:center;font-size:36px">ANALSE DES DONNEES DE TRAFIC, BRUIT, METEO ET SONDAGE</h1>

In [1]:
%load_ext autoreload
%autoreload 2

In [367]:
import sys
sys.path.append(r'C:\Users\martin.schoreisz\git\otv\otv\Transfert_Donnees')
sys.path.append(r'C:\Users\martin.schoreisz\git\Outils\Outils\src')
sys.path.append(r'C:\Users\martin.schoreisz\Box\Cerema\3E-Prod_Env_Risq\E6-Nuisances\E61-Acoustique\60-Etudes_Locales\2022-BruitRessentiBdxMet\4-Travaux_en_cours\donnees_produites\Codes\src\Carac_situ_acoustiq')
sys.path.append(r'C:\Users\martin.schoreisz\Box\Cerema\3E-Prod_Env_Risq\E6-Nuisances\E61-Acoustique\60-Etudes_Locales\2022-BruitRessentiBdxMet\4-Travaux_en_cours\donnees_produites\Codes\src')

import pandas as pd
import altair as alt
import numpy as np
from Import_stockage_donnees.Import_export_bdd import ResultatsEnquete
from Import_stockage_donnees.Params import dicoInstruSite
from Expoitation_mesures.Meteo import (recupDonneesMeteoBase, creerGraphMeteo, recupDonneesMeteofranceBase, 
                                       creerGraphCompVentSiteMeteoFrance, concatMeteoFranceEtSite, creerGraphCompConditionsPropa)
from Expoitation_mesures.Trafic import *
from Expoitation_mesures.Acoustique import recupDonneesAgregees, recupFractileAgregees
from Expoitation_mesures.Analyses_croises import (graphCroiseBruitMeteo1Jour, graphCroiseBruitMeteoPlusieursJour, graphCroiseBruitTrafic6min,
                                                  graphCroiseBruitMeteoTrafic, fusionnerDfSources, creerCorrelation)
from Bruit.Meteo import (DonneesMeteo, calculConditionPropagationMeteoFranceQualitatif, dicoSecteurAngulaire, conditionPropagation, calculGradientVitesseSon,
                         graphCompTempMesureeHautBas, calculCategorieVentQualitatif, secteurAngulaireQuantitatif, dfAngle)
from Bruit.Emission import Route
from Bruit.Niveaux import sommeEnergetique, niveau2Pression, sommeEnergetique, calculLden, calculTNI
from Trafic.Trafic_Routier import graphDebitVitesse1jour, graphDebitVitesseplusieursjour
from datetime import datetime, time
import locale
from Outils.Outils import dateTexteDepuisDayOfYear
from math import log10, pow, radians, pi, cos, sin, degrees

locale.setlocale(locale.LC_ALL, 'fr_FR')
pd.set_option('display.max_rows', 100)
pd.set_option('display.max_columns', 50)
pd.set_option('display.max_colwidth', 100)
alt.data_transformers.disable_max_rows()
# alt.data_transformers.enable('json')

# PARAMÈTRES

In [ ]:
tableMesuresBruitParSite = 'mesures_physiques.niveau_bruit_site'
attributSite = 'id_site'

## Analyse des données des déclarations de gene
Il s'agit de fournir des indicateurs de répartition des différentes valeurs de contexte et de déclaration fournies par les participants. Attention, les formulaires papiers ne permettaient pas de remplir tout les informations de contexte

<div class="alert alert-block alert-warning"><b>Attention:</b> Il n'y a pas d'analyse des commentaires réalisée pour le moment.</div>

In [ ]:
resultats = ResultatsEnquete()
resultats.creationCharts(export=False)
# si export = True, alors les données sont excportées dans le dossier dossierExportChartsRessenti du module Params

In [ ]:
# exemple
resultats.dicoCharts['localisation_gene']['chart']

# ANALYSE DES NIVEAUX DE BRUIT

## Niveaux reglementaires moyens

In [ ]:
# récupérer les données
dfReglementaireMoyen = pd.concat([recupDonneesAgregees(i, 'reg_lden_jour_moyen').drop_duplicates('leq_a').assign(
    periode=['Jour Ouvrés 6h-18h', 'Jour Ouvrés 18h-22h', 'Jour Ouvrés 22h-6h',
             'Samedi 6h-18h', 'Samedi 18h-22h', 'Samedi 22h-6h',
             'Dimanche 6h-18h', 'Dimanche 18h-22h', 'Dimanche 22h-6h']) for i in range(1, 5)]).replace({'id_instru_site': dicoInstruSite})

In [ ]:
alt.Chart(dfReglementaireMoyen, title=['Niveaux reglementaires moyens', '']).mark_bar().encode(
    x=alt.X('id_instru_site:N', title=None, sort=['Ladoumègue', 'Noyers', 'Villon', 'Ronsard']),
    y=alt.Y('leq_a:Q', title='Niveau de bruit', axis=alt.Axis(labelFontSize=15, titleFontSize=15)),
    color=alt.Color('id_instru_site:N', title='Sites', sort=['Ladoumègue', 'Noyers', 'Villon', 'Ronsard'], legend=alt.Legend(labelFontSize=12, titleFontSize=14)), 
    column=alt.Column('periode:N', spacing=40, sort=['Jour Ouvrés 6h-18h'], title=None, header=alt.Header(labelFontSize=12))).properties(width=75).configure_title(
        align='center', anchor='middle', fontSize=20).configure_axisX(disable=True)

In [ ]:
dfLden = dfReglementaireMoyen.pivot(index=['id_instru_site'], columns=['periode'], values='leq_a').reset_index()
dfLden['Jours ouvrés'] = dfLden.apply(lambda x: calculLden(x['Jour Ouvrés 6h-18h'], x['Jour Ouvrés 18h-22h'], x['Jour Ouvrés 22h-6h']), axis=1)
dfLden['Samedi'] = dfLden.apply(lambda x: calculLden(x['Samedi 6h-18h'], x['Samedi 18h-22h'], x['Samedi 22h-6h']), axis=1)
dfLden['Dimanche'] = dfLden.apply(lambda x: calculLden(x['Dimanche 6h-18h'], x['Dimanche 18h-22h'], x['Dimanche 22h-6h']), axis=1)
alt.Chart(dfLden.melt(id_vars='id_instru_site', value_vars=['Jours ouvrés', 'Samedi', 'Dimanche'], value_name='Niveau de bruit'),
          title=['Indicateur Lden moyen', '']).mark_bar().encode(
                        x=alt.X('id_instru_site', title=None, sort=['Ladoumègue', 'Noyers', 'Villon', 'Ronsard']),
                        y=alt.Y('Niveau de bruit', axis=alt.Axis(labelFontSize=15, titleFontSize=15)),
                        color=alt.Color('id_instru_site', sort=['Ladoumègue', 'Noyers', 'Villon', 'Ronsard'], title='Sites',
                                        legend=alt.Legend(labelFontSize=12, titleFontSize=14)),
                        column=alt.Column('periode', sort=['Jours ouvrés', 'Samedi', 'Dimanche'], spacing=40, title=None, header=alt.Header(labelFontSize=12))).properties(width=100).configure_title(
        align='center', anchor='middle', fontSize=20).configure_axisX(disable=True)

## variation des niveaux reglementaires selon la journée

In [ ]:
dfReglementaireParJour = pd.concat([recupDonneesAgregees(i, 'reglementaire_lden').set_index('date_heure').resample('60T').asfreq().bfill().reset_index()
                                    for i in range(1, 5)]).replace({'id_instru_site': dicoInstruSite})
dfReglementaireMoyen = pd.concat([recupDonneesAgregees(i, 'reg_lden_jour_moyen').set_index('date_heure').resample('60T').asfreq().bfill().reset_index() 
                                  for i in range(1, 5)]).replace({'id_instru_site': dicoInstruSite})
dfCompJourMoyRgelementaire = dfReglementaireParJour.merge(dfReglementaireMoyen, on=['date_heure', 'id_instru_site'], suffixes=['_jour', '_moy']
                             )
dfCompJourMoyRgelementaire['écart'] = dfCompJourMoyRgelementaire.leq_a_moy - dfCompJourMoyRgelementaire.leq_a_jour

In [ ]:
chartEvolutionNiveau = alt.Chart(dfReglementaireParJour, title=['Évolution des niveaux reglementaires', 'selon la journée']).mark_line().encode(
    x=alt.X('date_heure:T', title='jour', axis=alt.Axis(labelAngle=320)),
    y=alt.Y('leq_a:Q', title='niveau de bruit équivalent', scale=alt.Scale(domain=(35, 70)), axis=alt.Axis(labelFontSize=15, titleFontSize=15)),
    color=alt.Color('id_instru_site:N', sort=['Ladoumègue', 'Noyers', 'Villon', 'Ronsard'], title='Sites',
                    legend=alt.Legend(labelFontSize=12, titleFontSize=14))).properties(width=800)
chartEcart = alt.Chart(dfCompJourMoyRgelementaire, title=['Écart entre les moyennes des niveaux et', 'les niveaux réglementaire par jour']).mark_line().encode(
    x=alt.X('date_heure:T', title='jour', axis=alt.Axis(labelAngle=320)),
    y=alt.Y('écart:Q', title='écart de niveau', scale=alt.Scale(domain=(-8, 8), clamp=True), axis=alt.Axis(labelFontSize=15, titleFontSize=15)),
    color=alt.Color('id_instru_site:N', sort=['Ladoumègue', 'Noyers', 'Villon', 'Ronsard'], title='Sites',
                    legend=alt.Legend(labelFontSize=12, titleFontSize=14))).properties(width=800)
alt.vconcat(chartEvolutionNiveau, chartEcart).configure_title(
        align='center', anchor='middle', fontSize=20)

In [ ]:
((alt.Chart(dfCompJourMoyRgelementaire.loc[(dfCompJourMoyRgelementaire.id_instru_site == 'Ronsard') &
                                          (dfCompJourMoyRgelementaire.date_heure.dt.dayofweek.isin(range(5))) &
                                          (dfCompJourMoyRgelementaire.date_heure.dt.hour.isin(range(6,19)))], title='Ronsard').transform_density(
    'écart', as_=['écart', 'density']).mark_area().encode(
    x="écart:Q",
    y='density:Q',) | 
 alt.Chart(dfCompJourMoyRgelementaire.loc[(dfCompJourMoyRgelementaire.id_instru_site == 'Villon') & 
                                          (dfCompJourMoyRgelementaire.date_heure.dt.dayofweek.isin(range(5))) &
                                          (dfCompJourMoyRgelementaire.date_heure.dt.hour.isin(range(6,19)))], title='Villon').transform_density(
    'écart', as_=['écart', 'density']).mark_area().encode(
    x="écart:Q",
    y='density:Q',)) & (
 alt.Chart(dfCompJourMoyRgelementaire.loc[(dfCompJourMoyRgelementaire.id_instru_site == 'Ladoumègue') & 
                                          (dfCompJourMoyRgelementaire.date_heure.dt.dayofweek.isin(range(5))) &
                                          (dfCompJourMoyRgelementaire.date_heure.dt.hour.isin(range(6,19)))], title='Ladoumègue').transform_density(
    'écart', as_=['écart', 'density']).mark_area().encode(
    x="écart:Q",
    y='density:Q',) | 
 alt.Chart(dfCompJourMoyRgelementaire.loc[(dfCompJourMoyRgelementaire.id_instru_site == 'Noyers') & 
                                          (dfCompJourMoyRgelementaire.date_heure.dt.dayofweek.isin(range(5))) &
                                          (dfCompJourMoyRgelementaire.date_heure.dt.hour.isin(range(6,19)))], title='Noyers').transform_density(
    'écart', as_=['écart', 'density']).mark_area().encode(
    x="écart:Q",
    y=alt.Y('density:Q')))).properties(title=['Répartition des écarts entre niveaux journalier et', 'niveaux moyens']).configure_title(align='center', anchor='middle', fontSize=20)

## variation des niveaux reglementaires par jour et par pas de 30 minutes

In [ ]:
dfHoraire = recupDonneesAgregees(3, '30 min')
dfHoraire = dfHoraire.assign(heure_minute=dfHoraire.date_heure.apply(lambda x: f"{x.strftime('%H:%M')}"),
                        jour=dfHoraire.date_heure.apply(lambda x: x.strftime('%A %d %B %Y')),
                        jour_sort=dfHoraire.date_heure.dt.dayofyear)

In [ ]:
alt.Chart(dfHoraire, title=['Évolution du niveau de bruit', 'par pas de 30 minutes ; rue des Noyers']).mark_rect().encode(
    alt.X('heure_minute', title='Heure'),
    alt.Y('jour', sort=alt.EncodingSortField('jour_sort'), title='Jour'),
    color=alt.Color('leq_a:Q', legend=alt.Legend(title='Niveau de bruit'), scale=alt.Scale(bins=[c for c in range(50, 67, 2)],
                                                                                           domain=(50, 65)))).configure_title(
        align='center', anchor='middle', fontSize=20)

## variation des niveaux reglementaires par jour et par pas de 6 minutes

In [ ]:
df6Min = recupDonneesAgregees(3, '6 min')
df6Min['jour'] = df6Min.date_heure.dt.strftime('%Y-%m-%d _ %A')
dfReglementaireParJour = recupDonneesAgregees(3, 'reglementaire_lden').set_index('date_heure').resample('6T').asfreq().bfill().reset_index(
    ).replace({'periode_agreg': {'6 min': '6 minutes', 'reglementaire_lden': 'periode reglementaire'}})
dfReglementaireParJour['jour'] = dfReglementaireParJour.date_heure.dt.strftime('%Y-%m-%d _ %A')

In [ ]:
listJour = (88, 102, 101)
alt.Chart(pd.concat([df6Min.loc[df6Min.date_heure.dt.dayofyear.isin(listJour)],
           dfReglementaireParJour.loc[dfReglementaireParJour.date_heure.dt.dayofyear.isin(listJour)]]),
          title=["Évolution du niveau sonore selon la durée d'agrégation", "rue des Noyers"]).mark_line().encode(
    x=alt.X('hoursminutes(date_heure):T'), 
    y=alt.Y('leq_a', scale=alt.Scale(domain=[49,66]), axis=alt.Axis(labelFontSize=13, titleFontSize=12, title='Niveau de bruit')),
    color=alt.Color('periode_agreg:N', legend=alt.Legend(title="Durée d'agrégation")),
    row=alt.Row('jour', header=alt.Header(labelFontSize=12), title=None)).properties(width=600, height=150).configure_title(
        align='center', anchor='middle', fontSize=20)

In [ ]:
# dico des  datas
dicoChartsEcart={'6h-18h': {'bounds': range(7, 18)}, 
                 '18h-22h': {'bounds': range(19, 21)}, 
                 '22h-6h':{'bounds': [c for c in range(0,6)] + [23,] }}
# exmple de variation de niveau sur la période 6-18h, pour chaque jour de mesure
for k in dicoChartsEcart.keys():
    dicoChartsEcart[k]['df'] = df6Min.loc[(df6Min.date_heure.dt.hour.isin(dicoChartsEcart[k]['bounds']))].groupby(
        df6Min.date_heure.dt.dayofyear)['leq_a'].agg([min, max]).reset_index(
        ).merge(dfReglementaireParJour.loc[(dfReglementaireParJour.date_heure.dt.hour.isin(dicoChartsEcart[k]['bounds']))].groupby(
            dfReglementaireParJour.date_heure.dt.dayofyear)['leq_a'].agg(['mean']).reset_index().rename(columns={'mean': 'leq_reg'}), on='date_heure'
               ).sort_values('date_heure')
    dicoChartsEcart[k]['df']['écart Min-Max'] = dicoChartsEcart[k]['df']['max'] - dicoChartsEcart[k]['df']['min']
    dicoChartsEcart[k]['df']['jour'] = dicoChartsEcart[k]['df'].date_heure.apply(lambda x: datetime.strptime('2022' + "-" + str(x).rjust(3, '0'), "%Y-%j").strftime('%a %d %b'))
    base = alt.Chart(dicoChartsEcart[k]['df'], title=["Évolution de l'écart entre le minimum et le maximum", 
                                                      f"des niveauxde bruit agrégés par période de 6 minute ; rue des Noyers, {k}"]).encode(
        alt.X('jour', sort=alt.EncodingSortField('date_heure'),
              axis=alt.Axis(labelFontSize=13, titleFontSize=12, labelAngle=320)))
    dicoChartsEcart[k]['chartEcart'] = base.mark_line(color='green').encode(
        y=alt.Y('écart Min-Max',
                axis=alt.Axis(labelFontSize=13, titleFontSize=12, title='Écart min - max (db(A))', titleColor='green'),
                scale=alt.Scale(domain=(0, 20))))
    dicoChartsEcart[k]['chartReg'] = base.mark_line().encode(
        y=alt.Y('leq_reg',
                axis=alt.Axis(labelFontSize=13, titleFontSize=12, title=['Niveau sur la', 'période réglementaire'], titleColor='blue'),
                scale=alt.Scale(domain=(40, 70))))
    dicoChartsEcart[k]['chart'] = (dicoChartsEcart[k]['chartEcart'] + dicoChartsEcart[k]['chartReg']).resolve_scale(y='independent').properties(height=100)

In [ ]:
dicoChartsEcart['6h-18h']['chart'] & dicoChartsEcart['18h-22h']['chart'] & dicoChartsEcart['22h-6h']['chart']

### Visualisation 6 minutes globales

In [ ]:
# recup des donnees
dfPeriodeRegl = recupDonneesAgregees(3, 'reglementaire_lden')
df6Min = recupDonneesAgregees(3, '6 min')
df6Min['jour'] = df6Min.date_heure.dt.strftime('%Y-%m-%d _ %A')
dfPeriodeRegl['jour'] = dfPeriodeRegl.date_heure.dt.strftime('%Y-%m-%d _ %A')

In [ ]:
# visu
dfCompare6minRegl = pd.concat([pd.concat([dfPeriodeRegl.set_index('date_heure').resample('6T').asfreq().bfill().reset_index(), 
                               df6Min.reset_index()]).rename(
    columns={'day': 'jour', 'quantile': 'periode_agreg', 'value': 'leq_a'})])

In [ ]:
alt.Chart(dfCompare6minRegl).mark_line().encode(
    x=alt.X('hoursminutes(date_heure):T'), 
    y=alt.Y('leq_a', scale=alt.Scale(domain=[40,75])),
    color='periode_agreg:N').properties(width=300, height=250).facet('jour:N', columns=3).configure_axis(labelFontSize=13, titleFontSize=12)

## variation des niveaux sonores :  étude des indicateurs fractiles L10 et L90

### Période reglementaire

In [ ]:
dfFractileReg = recupFractileAgregees(3, 'reglementaire_lden')
dfFractileRegWide = dfFractileReg.pivot('date_heure', 'indicateur', 'valeur').reset_index()
dfFractileRegWide['diffL10L90'] = dfFractileRegWide.L10 - dfFractileRegWide.L90

In [ ]:
# variation des indicateurs fractile selon la journée et la période
df = (dfFractileReg.set_index(['date_heure', 'indicateur'])
                 .unstack(level=1).resample('60T')
                 .bfill()
                 .reset_index()
                 .drop(['id', 'periode_agreg', 'id_instru_site'], axis=1, level=0)
                 .T.reset_index(drop=True).T
                 .rename(columns={0: 'date_heure', 1: 'L10', 2: 'L50', 3: 'L90'}).merge(
                     dfReglementaireParJour.loc[dfReglementaireParJour.replace({'id_instru_site': dicoInstruSite}).id_instru_site == 'Noyers'], on='date_heure').melt(
                     id_vars='date_heure', value_vars=['L10', 'L50', 'L90', 'leq_a'], value_name='Niveau'))
base = alt.Chart(df,
                 title=["Évolutions des indicateurs L90 et L10 par période réglementaire ;", "rue des Noyers"], width=600).encode(
        x=alt.X('date_heure:T', axis=alt.Axis(labelFontSize=13, titleFontSize=12, title='Jour')),
        color=alt.Color('variable', title='Indicateurs'))
evolRegFractile = base.mark_line().encode(
    y=alt.Y('Niveau',
            scale=alt.Scale(zero=False),
            axis=alt.Axis(labelFontSize=13, titleFontSize=12, title='Niveau de bruit'))).transform_filter(
    "(datum.variable == 'L10') | (datum.variable == 'L90')").properties(width=800)
evolLeqReg = alt.Chart(df.loc[(df.variable == 'leq_a')]).mark_bar(width=0.5, color='grey').encode(
    x=alt.X('date_heure:T', axis=alt.Axis(labelFontSize=13, titleFontSize=12, title='Jour')),
    y=alt.Y('Niveau', scale=alt.Scale(zero=False), axis=alt.Axis(labelFontSize=13, titleFontSize=12, title='Niveau de bruit')))
chartEcart = alt.Chart(dfFractileRegWide, height=100, width=800, title="Différence L10 - L90").mark_line(color='green').encode(
    x=alt.X('date_heure:T', axis=alt.Axis(labelFontSize=13, titleFontSize=12, title='Jour')),
    y=alt.Y('diffL10L90',
            scale=alt.Scale(),
            axis=alt.Axis(labelFontSize=13, titleFontSize=12, title='Écart L10 - L90')))
((evolRegFractile + evolLeqReg) & chartEcart).configure_title(
        align='center', anchor='middle', fontSize=20)

In [ ]:
# répartition de l'écart entre L10 et L90
alt.hconcat(*[alt.Chart(dfFractileRegWide.loc[dfFractileRegWide.date_heure.dt.hour == hd],
                        title=["Répartition de l'écart entre les bruits majeurs", "et le bruit de fond ; rue des Noyers ;", f"période {hd}h-{hf}h"]).transform_density(
    'diffL10L90', as_=['diffL10L90', 'density']).mark_area().encode(
    x=alt.X("diffL10L90:Q", title='Écart L10 - L90'),
    y=alt.Y('density:Q', title='densité')).properties(width=300, height=200) for hd, hf in ((6, 18), (18, 22), (22, 6))])

### Période de 1 heure

In [ ]:
dfFractileHoraire = recupFractileAgregees(3, '1 h')
dfFractileHoraireWide = dfFractileHoraire.pivot('date_heure', 'indicateur', 'valeur').reset_index()
dfFractileHoraireWide['diffL10L90'] = dfFractileHoraireWide.L10 - dfFractileHoraireWide.L90

In [ ]:
df = dfFractileHoraireWide.merge(
                     dfReglementaireParJour.loc[dfReglementaireParJour.replace({'id_instru_site': dicoInstruSite}).id_instru_site == 'Noyers'], on='date_heure').melt(
                     id_vars='date_heure', value_vars=['L10', 'L50', 'L90', 'leq_a'], value_name='Niveau')
base = alt.Chart(df,
                 title=["Évolutions des indicateurs L90 et L10 par période de 1 heure ;", "rue des Noyers"], width=600).encode(
        x=alt.X('date_heure:T', axis=alt.Axis(labelFontSize=13, titleFontSize=12, title='Jour')),
        color=alt.Color('variable', title='Indicateurs'))
evolRegFractile = base.mark_line().encode(
    y=alt.Y('Niveau',
            scale=alt.Scale(zero=False),
            axis=alt.Axis(labelFontSize=13, titleFontSize=12, title='Niveau de bruit'))).transform_filter(
    "(datum.variable == 'L10') | (datum.variable == 'L90')").properties(width=800)
evolLeqReg = alt.Chart(df.loc[(df.variable == 'leq_a')]).mark_bar(width=0.5, color='grey').encode(
    x=alt.X('date_heure:T', axis=alt.Axis(labelFontSize=13, titleFontSize=12, title='Jour')),
    y=alt.Y('Niveau', scale=alt.Scale(zero=False), axis=alt.Axis(labelFontSize=13, titleFontSize=12, title='Niveau de bruit')))
chartEcart = alt.Chart(dfFractileHoraireWide, height=100, width=800, title="Différence L10 - L90").mark_line(color='green').encode(
    x=alt.X('date_heure:T', axis=alt.Axis(labelFontSize=13, titleFontSize=12, title='Jour')),
    y=alt.Y('diffL10L90',
            scale=alt.Scale(),
            axis=alt.Axis(labelFontSize=13, titleFontSize=12, title='Écart L10 - L90')))
((evolRegFractile + evolLeqReg) & chartEcart).configure_title(
        align='center', anchor='middle', fontSize=20)

In [ ]:
# répartition de l'écart entre L10 et L90
alt.hconcat(*[alt.Chart(dfFractileHoraireWide.loc[dfFractileHoraireWide.date_heure.dt.hour == hd],
                        title=["Répartition de l'écart entre les bruits majeurs", "et le bruit de fond ; rue des Noyers ;", f"période {hd}h-{hf}h"]).transform_density(
    'diffL10L90', as_=['diffL10L90', 'density']).mark_area().encode(
    x=alt.X("diffL10L90:Q", title='Écart L10 - L90'),
    y=alt.Y('density:Q', title='densité')).properties(width=300, height=200) for hd, hf in ((6, 18), (18, 22), (22, 6))])

### Période de 30 minutes

In [ ]:
dfFractile30Min = recupFractileAgregees(3, '30 min')
dfFractile30MinWide = dfFractile30Min.pivot('date_heure', 'indicateur', 'valeur').reset_index()
dfFractile30MinWide['diffL10L90'] = dfFractile30MinWide.L10 - dfFractile30MinWide.L90

In [ ]:
df = dfFractile30MinWide.merge(
    dfReglementaireParJour.loc[dfReglementaireParJour.replace({'id_instru_site': dicoInstruSite}).id_instru_site == 'Noyers'].set_index('date_heure').resample('30T').bfill().reset_index(), on='date_heure').melt(
    id_vars='date_heure', value_vars=['L10', 'L50', 'L90', 'leq_a', 'diffL10L90'], value_name='Niveau')

In [ ]:
base = alt.Chart(df,
                 title=["Évolutions des indicateurs L90 et L10 par périodes de 30 minutes ;", "rue des Noyers"], width=600).encode(
        x=alt.X('date_heure:T', axis=alt.Axis(labelFontSize=13, titleFontSize=12, title='Jour')),
        color=alt.Color('variable', title='Indicateurs'))
evolRegFractile = base.mark_line().encode(
    y=alt.Y('Niveau',
            scale=alt.Scale(zero=False),
            axis=alt.Axis(labelFontSize=13, titleFontSize=12, title='Niveau de bruit'))).transform_filter(
    "(datum.variable == 'L10') | (datum.variable == 'L90')").properties(width=800)
evolLeqReg = alt.Chart(df.loc[(df.variable == 'leq_a')]).mark_bar(width=0.5, color='grey').encode(
    x=alt.X('date_heure:T', axis=alt.Axis(labelFontSize=13, titleFontSize=12, title='Jour')),
    y=alt.Y('Niveau', scale=alt.Scale(zero=False), axis=alt.Axis(labelFontSize=13, titleFontSize=12, title='Niveau de bruit')))
chartEcart = alt.Chart(dfFractile30MinWide, height=100, width=800, title="Différence L10 - L90").mark_line(color='green').encode(
    x=alt.X('date_heure:T', axis=alt.Axis(labelFontSize=13, titleFontSize=12, title='Jour')),
    y=alt.Y('diffL10L90',
            scale=alt.Scale(),
            axis=alt.Axis(labelFontSize=13, titleFontSize=12, title='Écart L10 - L90')))
((evolRegFractile + evolLeqReg) & chartEcart).configure_title(
        align='center', anchor='middle', fontSize=20)

In [ ]:
# répartition de l'écart entre L10 et L90
alt.hconcat(*[alt.Chart(dfFractile30MinWide.loc[dfFractile30MinWide.date_heure.dt.hour == hd],
                        title=["Répartition de l'écart entre les bruits majeurs", "et le bruit de fond ; rue des Noyers ;", f"période {hd}h-{hf}h"]).transform_density(
    'diffL10L90', as_=['diffL10L90', 'density']).mark_area().encode(
    x=alt.X("diffL10L90:Q", title='Écart L10 - L90'),
    y=alt.Y('density:Q', title='densité')).properties(width=300, height=200) for hd, hf in ((6, 18), (18, 22), (22, 6))])

In [ ]:
dfChart = df.pivot('date_heure', 'variable', 'Niveau').reset_index().assign(heure_minute=df.date_heure.apply(lambda x: f"{x.strftime('%H:%M')}"),
                        jour=df.date_heure.apply(lambda x: x.strftime('%A %d %B %Y')),
                        jour_sort=df.date_heure.dt.dayofyear)
for c in ['L90', 'L10', 'diffL10L90']:
    dfChart[c] = dfChart[c].astype(int)
base = alt.Chart(dfChart).mark_rect().encode(
    alt.X('heure_minute:N', title='Heure'),
    alt.Y('jour', sort=alt.EncodingSortField('jour_sort'), title='Jour'),
    color=alt.Color('L90:Q', legend=alt.Legend(title=['Niveau de bruit', 'de fond']), scale=alt.Scale(bins=[c for c in range(50, 67, 2)],
                                                                                           domain=(50, 65))))
text = base.mark_text(baseline='middle').encode(
    text='diffL10L90:Q',
    color=alt.condition(
        alt.datum.diffL10L90 >= 10,
        alt.value('red'),
        alt.value('black')))
(base + text).properties(width=1000, title=['Niveaux de bruit de fond et différence bruit de fond - bruit forts ;', 'par jour et par 30 minutes, pour les riverains de la rue Jules Ladoumegue']).configure_title(
        align='center', anchor='middle', fontSize=20)

### Période de 6 minutes

In [ ]:
dfFractile6Min = recupFractileAgregees(3, '6 min')
dfFractile6MinWide = dfFractile6Min.pivot('date_heure', 'indicateur', 'valeur').reset_index()
dfFractile6MinWide['diffL10L90'] = dfFractile6MinWide.L10 - dfFractile6MinWide.L90

In [ ]:
df = dfFractile6MinWide.merge(
    dfReglementaireParJour.loc[dfReglementaireParJour.replace({'id_instru_site': dicoInstruSite}).id_instru_site == 'Noyers'].set_index('date_heure').resample('6T').bfill().reset_index(), on='date_heure').melt(
    id_vars='date_heure', value_vars=['L10', 'L50', 'L90', 'leq_a', 'diffL10L90'], value_name='Niveau')

In [ ]:
base = alt.Chart(df,
                 title=["Évolutions des indicateurs L90 et L10 par périodes de 30 minutes ;", "rue des Noyers"], width=600).encode(
        x=alt.X('date_heure:T', axis=alt.Axis(labelFontSize=13, titleFontSize=12, title='Jour')),
        color=alt.Color('variable', title='Indicateurs'))
evolRegFractile = base.mark_line().encode(
    y=alt.Y('Niveau',
            scale=alt.Scale(domain=(35,75), clamp=True),
            axis=alt.Axis(labelFontSize=13, titleFontSize=12, title='Niveau de bruit'))).transform_filter(
    "(datum.variable == 'L10') | (datum.variable == 'L90')").properties(width=1500)
evolLeqReg = alt.Chart(df.loc[(df.variable == 'leq_a')]).mark_bar(width=0.1, color='grey').encode(
    x=alt.X('date_heure:T', axis=alt.Axis(labelFontSize=13, titleFontSize=12, title='Jour')),
    y=alt.Y('Niveau', scale=alt.Scale(zero=False), axis=alt.Axis(labelFontSize=13, titleFontSize=12, title='Niveau de bruit')))
chartEcart = alt.Chart(dfFractile6MinWide, height=100, width=1500, title="Différence L10 - L90").mark_line(color='green').encode(
    x=alt.X('date_heure:T', axis=alt.Axis(labelFontSize=13, titleFontSize=12, title='Jour')),
    y=alt.Y('diffL10L90',
            scale=alt.Scale(),
            axis=alt.Axis(labelFontSize=13, titleFontSize=12, title='Écart L10 - L90')))
((evolRegFractile + evolLeqReg) & chartEcart).configure_title(
        align='center', anchor='middle', fontSize=20)

In [ ]:
# répartition de l'écart entre L10 et L90
alt.hconcat(*[alt.Chart(dfFractile6MinWide.loc[dfFractile6MinWide.date_heure.dt.hour == hd],
                        title=["Répartition de l'écart entre les bruits majeurs", "et le bruit de fond ; rue des Noyers ;", f"période {hd}h-{hf}h"]).transform_density(
    'diffL10L90', as_=['diffL10L90', 'density']).mark_area().encode(
    x=alt.X("diffL10L90:Q", title='Écart L10 - L90'),
    y=alt.Y('density:Q', title='densité')).properties(width=300, height=200) for hd, hf in ((6, 18), (18, 22), (22, 6))])

### indicateur TNI
indicatuer basé sur la diff L10-90

In [ ]:
dfFractileRegWide['TNI'] = dfFractileRegWide.apply(lambda x: calculTNI(x.L10, x.L90), axis=1)

In [ ]:
df = (dfFractileRegWide.merge(dfReglementaireParJour.loc[dfReglementaireParJour.replace({'id_instru_site': dicoInstruSite}).id_instru_site == 'Noyers'], on='date_heure')
          .set_index('date_heure')
          .resample('60T')
          .bfill()
          .reset_index()
          .melt(id_vars='date_heure', value_vars=['L10', 'L50', 'L90', 'leq_a', 'TNI'], value_name='Niveau'))
baseTNI = alt.Chart(df,
                    title=["Évolutions des indicateurs TNI et Laeq par période réglementaire ;", "rue Jules Ladoumègue"], width=600).encode(
        x=alt.X('date_heure:T', axis=alt.Axis(labelFontSize=13, titleFontSize=12, title='Jour')),
        color=alt.Color('variable', title='Indicateurs', legend=alt.Legend(labelFontSize=12, titleFontSize=14)))
evolRegTNI = baseTNI.mark_line().encode(
    y=alt.Y('Niveau',
            scale=alt.Scale(zero=False),
            axis=alt.Axis(labelFontSize=13, titleFontSize=12, title='Niveau de bruit'))).transform_filter(
    "(datum.variable == 'TNI') | (datum.variable == 'leq_a')").properties(width=800).configure_title(
        align='center', anchor='middle', fontSize=20)

In [ ]:
evolRegTNI

## Recherche de dépassement de valeurs seuil

In [ ]:
# exempe des données 6 minutes
# import des données 
df6MinSite = recupDonneesAgregees(3, '6 min')

In [ ]:
def depassementSeuilReglementaire(horodate, niveau, typeReglementation='france'):
    """
    renvoyer un booleen si un niveau depasse un seuil reglementaire, en fonoction du type de reglementation
    in : 
        horodate : datetime. moment dans une journée.
        niveau : numeric. niveaude bruit, peu importe l'indicateur
        typeReglementation : string. 'france' ou 'europe'.
    """
    if typeReglementation == 'france':
        if (time(6, 0, 0) <= horodate.time() <= time(22, 0, 0)) and niveau >= 70:
            return True
        elif (horodate.time() <= time(6, 0, 0) or horodate.time() > time(22, 0, 0)) and niveau >= 65:
            return True
        else:
            return False
df6MinSite['depassement_reglementaire'] = df6MinSite.apply(lambda x: depassementSeuilReglementaire(x.date_heure, x.leq_a), axis=1)

In [ ]:
df6MinSite.loc[df6MinSite.depassement_reglementaire == True]

# ANALYSE DE LA MÉTÉO

## meteo france

In [ ]:
dfMeteoFranceBx = recupDonneesMeteofranceBase().set_index('date_3heures').resample('30T').bfill().reset_index()
dfMeteoFranceBx = dfMeteoFranceBx.loc[dfMeteoFranceBx.date_3heures.isin(pd.date_range('2022-03-21', '2022-04-19', freq='30T'))].copy()
dfMeteoFranceBx = calculConditionPropagationMeteoFranceQualitatif(dfMeteoFranceBx, 90, (7, 30), (20, 30)).rename(columns={'date_3heures': 'date_heure'})

## meteo mesurée

In [729]:
# récupération des données sources
dfMeteoBase = recupDonneesMeteoBase()
# intialisation de l'objet
meteo = DonneesMeteo(dfMeteoBase, 1, 3, 30, '2022-03-21 13:30:00', 3)
# analyse selon les angles source recepteur# dans le cas du site id_instru_site = 3 : la liaison émetteeur - recepteur est à 0 pour la partie visible au nord, ou 90
angleEmmeteurRecepteur1, angleEmmeteurRecepteur2 = 0, 90
dfMeteo, dfAnglesOrienteRecepteurs = meteo.propagationSourceRecepteurRiverain(meteo.dfAngleGradient, angleEmmeteurRecepteur1, angleEmmeteurRecepteur2)

In [732]:
dfMeteo.loc[dfMeteo.date_heure.dt.dayofyear == 101]

date_heure  vts_vent_haut  vit_vent_bas  temp_haut   temp_bas  \
11785 2022-04-11 00:00:00       2.325333      1.435333  13.964300  13.217567   
11797 2022-04-11 00:30:00       2.997333      2.081000  13.476600  12.944533   
11809 2022-04-11 01:00:00       2.946667      2.165000  13.040233  12.600467   
11821 2022-04-11 01:30:00       3.181000      2.350667  12.914767  12.526200   
11833 2022-04-11 02:00:00       2.274333      1.452333  12.287700  11.809633   
11845 2022-04-11 02:30:00       1.762333      0.974333  11.856467  11.362633   
11857 2022-04-11 03:00:00       1.897000      1.183333  11.575067  11.170500   
11869 2022-04-11 03:30:00       2.450000      1.545333  11.413833  11.063233   
11881 2022-04-11 04:00:00       1.998000      1.217333  11.137967  10.761467   
11893 2022-04-11 04:30:00       1.519000      0.772333  10.880300  10.428800   
11905 2022-04-11 05:00:00       1.628667      0.915000  10.681633  10.236900   
11917 2022-04-11 05:30:00       1.553000      0.831333  10.480233  10.071933   
11929 2022-04-11 06:00:00       1.846333      1.142333  10.552267  10.206767   
11941 2022-04-11 06:30:00       2.098000      1.343333  10.595400  10.307233   
11953 2022-04-11 07:00:00       1.939000      1.251000  10.613200  10.344033   
11965 2022-04-11 07:30:00       1.905000      1.267333  10.650567  10.373300   
11977 2022-04-11 08:00:00       2.139333      1.411000  11.016800  10.850767   
11989 2022-04-11 08:30:00       3.668667      2.703000  11.583900  11.494100   
12001 2022-04-11 09:00:00       3.845000      2.861333  12.009300  11.990633   
12013 2022-04-11 09:30:00       3.567000      2.795667  13.115400  13.417033   
12025 2022-04-11 10:00:00       2.492333      1.586333  13.905067  14.405967   
12037 2022-04-11 10:30:00       3.089333      2.250000  14.569067  15.079100   
12049 2022-04-11 11:00:00       2.416333      1.620667  15.802367  16.448300   
12060 2022-04-11 11:30:00       2.332667      1.258667  16.640033  17.583933   
12073 2022-04-11 12:00:00       2.290333      1.260333  17.571933  18.662733   
12084 2022-04-11 12:30:00       2.459333      1.527667  18.062767  18.877600   
12097 2022-04-11 13:00:00       2.718667      1.931000  19.377867  20.323400   
12109 2022-04-11 13:30:00       3.223333      2.376000  20.122633  20.938900   
12120 2022-04-11 14:00:00       2.173000      1.210000  21.100900  21.944567   
12133 2022-04-11 14:30:00       2.870333      1.896333  21.337233  22.043533   
12144 2022-04-11 15:00:00       2.459667      1.527667  21.747100  22.315633   
12157 2022-04-11 15:30:00       3.046000      2.116333  22.042733  22.682867   
12169 2022-04-11 16:00:00       3.365667      2.351333  22.178900  22.747767   
12181 2022-04-11 16:30:00       3.718333      2.686000  22.165433  22.603300   
12192 2022-04-11 17:00:00       3.249333      2.173000  21.926300  22.272500   
12204 2022-04-11 17:30:00       2.896667      1.821333  21.463567  21.719967   
12216 2022-04-11 18:00:00       3.232333      2.214333  20.539400  20.377467   
12228 2022-04-11 18:30:00       2.821000      1.762667  20.102133  19.821200   
12240 2022-04-11 19:00:00       3.081333      1.879333  19.067133  18.608033   
12252 2022-04-11 19:30:00       2.493333      1.501333  18.130167  17.595100   
12264 2022-04-11 20:00:00       2.283000      1.209667  17.265900  16.705933   
12276 2022-04-11 20:30:00       2.534667      1.368667  16.669467  16.167500   
12288 2022-04-11 21:00:00       2.484000      1.410667  15.938700  15.361200   
12300 2022-04-11 21:30:00       2.183333      1.225333  15.366000  14.766900   
12312 2022-04-11 22:00:00       2.644333      1.619333  14.892800  14.377400   
12324 2022-04-11 22:30:00       2.812000      1.947333  14.331233  13.854000   
12336 2022-04-11 23:00:00       2.316333      1.602667  13.803500  13.326600   
12348 2022-04-11 23:30:00       2.072333      1.511000  13.357067  12.827133   

       temp_haut_k  temp_bas_k  dir_vent_haut  dir_vent_bas  hygro_haut  \
11785   288.114300 

In [730]:
# graphs conditions météo (posiblede générer pour un jour ou plusieurs)
creerGraphMeteo(dfMeteo, jour=101)

alt.VConcatChart(...)

In [ ]:
# pour info, graph de variation de température
graphCompTempMesureeHautBas(dfMeteo, 300, 150)

## comparaison meteoFrance meteo mesurée

In [ ]:
# pour info
dfMeteoCompRiverain = concatMeteoFranceEtSite(dfMeteo, dfMeteoFranceBx)
creerGraphCompConditionsPropa(dfMeteo, dfMeteoFranceBx, 1200)

In [ ]:
creerGraphCompVentSiteMeteoFrance(dfMeteoCompRiverain, jour=None, largeur=800, hauteur=150)

# ANALYSE CROISEE METEO / BRUIT

In [64]:
# récupération des données
# bruit
dfBruit = recupDonneesAgregees(3, '30 min')
# meteo
dfMeteoBase = recupDonneesMeteoBase()
meteo = DonneesMeteo(dfMeteoBase, 1, 3, 30, '2022-03-21 13:00:00', 3)
angleEmmeteurRecepteur1, angleEmmeteurRecepteur2 = 0, 90
dfMeteo, dfAnglesOrienteRecepteurs = meteo.propagationSourceRecepteurRiverain(meteo.dfAngleGradient, angleEmmeteurRecepteur1, angleEmmeteurRecepteur2)

In [65]:
dfBruitMeteo = (dfBruit[['date_heure', 'leq_a']]
                .assign(heure_minute=dfBruit.date_heure.apply(lambda x: f"{x.strftime('%H:%M')}"),
                        jour=dfBruit.date_heure.apply(lambda x: x.strftime('%A %d %B %Y')),
                        jour_sort=dfBruit.date_heure.dt.dayofyear)
                .merge(dfMeteo[['date_heure', 'ConditionPropagation', 'grad_moy', 'temp_haut', 'dir_vent_haut',
                                'forcePropagation_txt', 'forcePropagation_num', 'vts_vent_haut', 'pluie', 'rayonnement']], on='date_heure')) 

In [66]:
# graph de relation bruit / météo
# paramètres
domainBruit = (48, 68)
largeur = 450
hauteur = 200
rangeMin = dfBruitMeteo.forcePropagation_num.min() * 8000
rangeMax = dfBruitMeteo.forcePropagation_num.max() * 20
domainMax = dfBruitMeteo.forcePropagation_num.max()

In [67]:
# graphs sur 1 jour
graphCroiseBruitMeteo1Jour(dfBruitMeteo, 104, domainBruit, rangeMin, rangeMax, domainMax,
                                   largeur, hauteur, configure=True)

In [68]:
# graphs de comparaison (si besoin de 1 seul jour utilisé graphCroiseBruitMeteo1Jour()) sur des jousr choisis
jour1, jour2 = 104, 105
graphCroiseBruitMeteoPlusieursJour(dfBruitMeteo, [jour1, jour2], domainBruit, rangeMin, rangeMax, domainMax,
                                   largeur, hauteur, configure=True)

In [735]:
# graphs de comparaison (si besoin de 1 seul jour utilisé graphCroiseBruitMeteo1Jour()) sur l'ensemble des jours
graphCroiseBruitMeteoPlusieursJour(dfBruitMeteo, [e for e in range(80,108)], domainBruit, rangeMin, rangeMax, domainMax,
                                   400, 200, configure=True)

alt.VConcatChart(...)

In [738]:
# Rose des vents
# paramètres
dureePériode = 6  # durée ejn minute de regrouepement et moyennage de la météo
angleSourRecepteur = 0
# récupération des données
# initialisation de la météo
dfMeteoBase = recupDonneesMeteoBase()
meteo = DonneesMeteo(dfMeteoBase, 1, 3, 6, '2022-03-21 13:00:00', 3)

In [742]:
# prahique d'occurence de la provenance du vent
dfOrientVent, chartOrientVent = meteo.graphOccurenceOrientationVent(400, 300)
chartOrientVent

alt.LayerChart(...)

In [750]:
# pourcentage d'occurence favorable et défavorable pour les direction de provenance du vent
dfTxOccurenceConditions, chartOccurenceConditionsSecteur = meteo.graphOccurenceConditionParSecteur(400, 400)
chartOccurenceConditionsSecteur

alt.LayerChart(...)

In [746]:
dfTxOccurenceConditions.head(5)

angle_min  angle_minRad  angle_maxRad Conditions de propagation  Occurence  \
0        0.0      0.000000      0.349066               Défavorable   0.362417   
1       20.0      0.349066      0.698132               Défavorable   0.351745   
2       40.0      0.698132      1.047198               Défavorable   0.376406   
3       60.0      1.047198      1.396263               Défavorable   0.397029   
4       80.0      1.396263      1.745329               Défavorable   0.426305   

    radius2 text_legende  
0  0.352417         Nord  
1  0.341745          NaN  
2  0.366406          NaN  
3  0.387029          NaN  
4  0.416305          Est

In [747]:
meteo.dfAngleGradient

date_heure  vts_vent_haut  vit_vent_bas  temp_haut   temp_bas  \
0     2022-03-21 13:18:00       2.936667      1.426667     18.937  19.880667   
1     2022-03-21 13:18:00       2.936667      1.426667     18.937  19.880667   
2     2022-03-21 13:18:00       2.936667      1.426667     18.937  19.880667   
3     2022-03-21 13:18:00       2.936667      1.426667     18.937  19.880667   
4     2022-03-21 13:18:00       2.936667      1.426667     18.937  19.880667   
...                   ...            ...           ...        ...        ...   
83323 2022-04-19 11:36:00       0.501667      0.166667     12.175  12.457000   
83324 2022-04-19 11:36:00       0.501667      0.166667     12.175  12.457000   
83325 2022-04-19 11:36:00       0.501667      0.166667     12.175  12.457000   
83326 2022-04-19 11:36:00       0.501667      0.166667     12.175  12.457000   
83327 2022-04-19 11:36:00       0.501667      0.166667     12.175  12.457000   

       temp_haut_k  temp_bas_k  dir_vent_haut  dir_vent_bas  hygro_haut  \
0          293.087  294.030667      93.566667    265.333333   53.733333   
1          293.087  294.030667      93.566667    265.333333   53.733333   
2          293.087  294.030667      93.566667    265.333333   53.733333   
3          293.087  294.030667      93.566667    265.333333   53.733333   
4          293.087  294.030667      93.566667    265.333333   53.733333   
...            ...         ...            ...           ...         ...   
83323      286.325  286.607000     295.983333    305.583333   87.033333   
83324      286.325  286.607000     295.983333    305.583333   87.033333   
83325      286.325  286.607000     295.983333    305.583333   87.033333   
83326      286.325  286.607000     295.983333    305.583333   87.033333   
83327      286.325  286.607000     295.983333    305.583333   87.033333   

       hygro_bas  rayonnement  pluie       a_w       a_t  gradient_vits  \
0      55.733333   671.466667    0.0  1.374461 -0.858962       0.458154   
1      55.733333   671.466667    0.0  1.374461 -0.858962       0.458154   
2      55.733333   671.466667    0.0  1.374461 -0.858962       0.458154   
3      55.733333   671.466667    0.0  1.374461 -0.858962       0.458154   
4      55.733333   671.466667    0.0  1.374461 -0.858962       0.458154   
...          ...          ...    ...       ...       ...            ...   
83323  88.400000   175.833333    0.0  0.304930 -0.256687       0.101643   
83324  88.400000   175.833333    0.0  0.304930 -0.256687       0.101643   
83325  88.400000   175.833333    0.0  0.304930 -0.256687       0.101643   
83326  88.400000   175.833333    0.0  0.304930 -0.256687       0.101643   
83327  88.400000   175.833333    0.0  0.304930 -0.256687       0.101643   

       gradient_temp  angle_min  angle_max  grad_min  grad_max  grad_moy  \
0          -0.286321          0         30  0.290497  0.228847  0.274751   
1          -0.286321         30         60  0.229116  0.061151  0.156172   
2          -0.286321         60         90  0.061420 -0.167926 -0.049212   
3          -0.286321         90        120 -0.167657 -0.397003 -0.286370   
4          -0.286321        120        150 -0.396733 -0.564699 -0.491755   
...              ...        ...        ...       ...       ...       ...   
83323      -0.085562        210        240 -0.138772 -0.101593 -0.122631   
83324      -0.085562        240        270 -0.101568 -0.050771 -0.077066   
83325      -0.085562        270        300 -0.050746  0.000050 -0.024451   
83326      -0.085562        300        330  0.000075  0.037255  0.021114   
83327      -0.085562        330        360  0.037279  0.050872  0.047421   

      ConditionPropagation  
0                favorable  
1                favorable  
2              defavorable  
3              defavorable  
4              defavorable  
...                    ...  
83323          defavorable  
83324          defavorable  
83325          defavorable  
83326            favorable  
83327            fav

# ANALYSE TRAFICS

## viabilité des données fournies, analyse des données 6 minutes 
Dans ce chapitre, on va se concentrer sur l'analyse des diagrammes Débit / Vitesses, pour obtenir la liste des jours et voies sans pb dans les données fournies

In [757]:
# récupération d'un site instrumenté et mise en forme des données
voie = ['section courante']
dfDebitVitesseVoiesBdd = recupDonneesTraficBase(8, voie=voie, indicateur=['TV', 'Vmoy_TV'])
dfDebitVitesseVoiesBddWide = dfDebitVitesseVoiesBdd.pivot(index=['date_heure', 'voie', 'sens'], columns='indicateur', values='valeur').reset_index()

In [758]:
# analyse d'une journée
graphDebitVitesse1jour(dfDebitVitesseVoiesBddWide, 105, voie, 'sens exter', largeur=320, hauteur=300)

alt.HConcatChart(...)

In [765]:
# analyse de l'ensemble des journée
graphDebitVitesseplusieursjour(dfDebitVitesseVoiesBddWide, [j for j in range(80, 109)], voie, 'sens inter', largeur=300, hauteur=150)

alt.VConcatChart(...)

## Représentation et analyse des données 
à partir de la liste des jours OK, on peut dresser la représentation par voie et 2 voies confondus des débits et vitesses pour les VL et PL

In [766]:
# récupération des données 6 minutes de trafic
df6MinParSens = recupTraficEtVitesse6MinParSens(8, ['section courante',])

In [767]:
df6MinParSens

date_heure  id_instru_site        sens              voie  \
0     2022-03-21 00:06:00               8  sens exter  section courante   
1     2022-03-21 00:12:00               8  sens exter  section courante   
2     2022-03-21 00:18:00               8  sens exter  section courante   
3     2022-03-21 00:24:00               8  sens exter  section courante   
4     2022-03-21 00:30:00               8  sens exter  section courante   
...                   ...             ...         ...               ...   
28751 2022-04-19 23:54:00               8  sens inter  section courante   
28752 2022-04-20 00:00:00               8  sens exter  section courante   
28753 2022-04-20 00:00:00               8  sens exter  section courante   
28754 2022-04-20 00:00:00               8  sens inter  section courante   
28755 2022-04-20 00:00:00               8  sens inter  section courante   

      indicateur     valeur heure_minute                    jour  jour_sort  
0      vitessePL  77.900000        00:06      lundi 21 mars 2022         80  
1      vitessePL  85.500000        00:12      lundi 21 mars 2022         80  
2      vitessePL  84.550000        00:18      lundi 21 mars 2022         80  
3      vitessePL  85.500000        00:24      lundi 21 mars 2022         80  
4      vitessePL  82.650000        00:30      lundi 21 mars 2022         80  
...          ...        ...          ...                     ...        ...  
28751         VL  33.510345        23:54     mardi 19 avril 2022        109  
28752         PL  40.909091        00:00  mercredi 20 avril 2022        110  
28753         VL  54.090909        00:00  mercredi 20 avril 2022        110  
28754         PL  25.158287        00:00  mercredi 20 avril 2022        110  
28755         VL  44.841713        00:00  mercredi 20 avril 2022        110  

[57512 rows x 9 columns]

In [770]:
# graph de visu des volumes et vitesses
graphTraficVitesseEmission2SensSepares(df6MinParSens, "Section courante Rocade Nord", emission_bruit=False)

ValidationError: 'Section courante Rocade Nord' is not of type 'number'

Failed validating 'type' in schema[0]:
    {'type': 'number'}

On instance:
    'Section courante Rocade Nord'

In [ ]:
# analyse de la répartition des trafics
# Donnees générales
df6MinTVParSens = recupDonneesTraficBase(7, voie=['section courante'], indicateur=['TV'], periodeAgreg=['6 min'])
df6MinTVParSens = (df6MinTVParSens
                   .assign(jour_semaine=df6MinTVParSens.date_heure.dt.dayofweek,
                           heure_minute=df6MinTVParSens.date_heure.apply(lambda x: f"{x.strftime('%H:%M')}"),
                           jour=df6MinTVParSens.date_heure.apply(lambda x: x.strftime("%A %d %B %Y")),
                           jour_sort=df6MinTVParSens.date_heure.dt.dayofyear)).sort_values('jour_sort')
df6MinTVParSens = df6MinTVParSens.loc[~df6MinTVParSens.jour_sort.isin((108, 109, 110))]
# limitation aux jours ouvres, samedi ou dimanche
df6MinTVParSensJoursOuvres = df6MinTVParSens.loc[df6MinTVParSens.jour_semaine.isin(range(5))] 
df6MinTVParSensSamedi = df6MinTVParSens.loc[df6MinTVParSens.jour_semaine == 5]
df6MinTVParSensDimanche = df6MinTVParSens.loc[df6MinTVParSens.jour_semaine == 6]
# graphs
graphTVTousJO = graphTVTousJours(df6MinTVParSensJoursOuvres, ['Trafic tous véhicules par pas de 6 minutes', 'tous jours ouvrés'], largeur=800)
graphTVTousSamedi = graphTVTousJours(df6MinTVParSensSamedi, ['Trafic tous véhicules par pas de 6 minutes', 'tous Samedi'], largeur=800)
graphTVTousDimanche = graphTVTousJours(df6MinTVParSensDimanche, ['Trafic tous véhicules par pas de 6 minutes', 'tous Dimanche'], largeur=800)

In [ ]:
graphTVTousJO

In [ ]:
# filtredes jours avant le WE de Pâques
dfJoursOuvresAvantPaque = df6MinTVParSensJoursOuvres.loc[~df6MinTVParSensJoursOuvres.jour_sort.isin((105, 106, 107))]

graphTVEcartJoursOuvres = graphStatTVTousJours(dfJoursOuvresAvantPaque,
                                             f"Statistiques et trafic par jour et période de 6 minutes ; jours ouvrés hors période de Pâques")
graphTVEcartSamedi = graphStatTVTousJours(df6MinTVParSensSamedi,
                                        f"Statistiques et trafic par jour et période de 6 minutes ; Samedi")
graphTVEcartDimanche = graphStatTVTousJours(df6MinTVParSensDimanche,
                                          f"Statistiques et trafic par jour et période de 6 minutes ; Dimanche")

In [ ]:
graphTVEcartDimanche

In [ ]:
# analyse de la répartition des vitesses
df6MinVitessesParSens = df6MinParSens.loc[df6MinParSens.indicateur.isin(('vitesseVL', 'vitessePL')) & (~df6MinParSens.jour_sort.isin((108, 109, 110)))].copy()

In [ ]:
df6MinVitessesParSens = (df6MinVitessesParSens
                         .assign(jour_semaine=df6MinVitessesParSens.date_heure.dt.dayofweek,
                                 heure_minute=df6MinVitessesParSens.date_heure.apply(lambda x: f"{x.strftime('%H:%M')}"),
                                 jour=df6MinVitessesParSens.date_heure.apply(lambda x: x.strftime("%A %d %B %Y")),
                                 jour_sort=df6MinVitessesParSens.date_heure.dt.dayofyear)).sort_values('jour_sort')
# limitation aux jours ouvres, samedi ou dimanche

df6MinVitessesParSensJoursOuvres = df6MinVitessesParSens.loc[df6MinVitessesParSens.jour_semaine.isin(range(5))] 
df6MinVitessesParSensSamedi = df6MinVitessesParSens.loc[df6MinVitessesParSens.jour_semaine == 5]
df6MinVitessesParSensDimanche = df6MinVitessesParSens.loc[df6MinVitessesParSens.jour_semaine == 6]

In [ ]:
graphVitessesTousJours(df6MinVitessesParSensJoursOuvres,
                       ['Vitesses tous véhicules par pas de 6 minutes', 'tous JO'])

In [ ]:
# filtredes jours avant le WE de Pâques
dfVitesseJoursOuvresAvantPaque = df6MinVitessesParSensJoursOuvres.loc[~df6MinVitessesParSensJoursOuvres.jour_sort.isin((105, 106, 107))]
graphStatVitesseTousJours(dfVitesseJoursOuvresAvantPaque, 'Vitesses : Moyenne et évolution selon un écart type ou 10 km/h', largeur=600)

In [ ]:
df6MinParSens

### Niveaux d'émissions

In [ ]:
# PARAMS
# attention, 
# la declivité dépend du site et du sens de mesure
# l'age dépend du site et du sens de mesure
dfEmissionTheorique = df6MinParSens.pivot(index = ['date_heure', 'sens', 'heure_minute', 'jour', 'jour_sort'], columns='indicateur', values='valeur').reset_index()
dfEmissionTheorique['declivite'] = dfEmissionTheorique.apply(lambda x: -3 if x.sens == 'sens inter' else 3, axis=1)
dfEmissionTheorique['age_rvt'] = dfEmissionTheorique.apply(lambda x: 6 if x.sens == 'sens inter' else 5, axis=1)
dfEmissionTheorique['emission_bruit'] = dfEmissionTheorique.apply(
    lambda x : Route(x.VL, x.PL, x.vitesseVL, x.vitessePL, 'r3', x.age_rvt, 's', x.declivite, ignoreErreurVts=True).lwm, axis=1)
# mis en forme pour graph
dfChartEmission = dfEmissionTheorique.melt(id_vars=['date_heure', 'sens', 'heure_minute', 'jour', 'jour_sort'], 
                                           value_vars=['PL', 'VL', 'vitessePL', 'vitesseVL', 'emission_bruit'],
                                           var_name='indicateur', value_name='valeur')
# emission par sens et ajout de la'ttribut pour filtre des catégorie de jours
dfChartEmission = dfChartEmission.assign(jour_semaine=dfChartEmission.date_heure.dt.dayofweek)
dfChartEmissionJoursOuvres = dfChartEmission.loc[(dfChartEmission.indicateur == 'emission_bruit') & (~dfChartEmission.jour_sort.isin((108, 109, 110)))
                    & (dfChartEmission.jour_semaine.isin(range(5)))]
dfChartEmissionSamedi = dfChartEmission.loc[(dfChartEmission.indicateur == 'emission_bruit') & (~dfChartEmission.jour_sort.isin((108, 109, 110)))
                    & (dfChartEmission.jour_semaine == 5)]
dfChartEmissionDimanche = dfChartEmission.loc[(dfChartEmission.indicateur == 'emission_bruit') & (~dfChartEmission.jour_sort.isin((108, 109, 110)))
                    & (dfChartEmission.jour_semaine == 6)]
dfChartEmission2Sens = dfChartEmission.loc[dfChartEmission.indicateur == 'emission_bruit'].groupby(
            ['date_heure', 'heure_minute', 'jour', 'jour_sort','jour_semaine', 'indicateur']).valeur.apply(
            lambda x : sommeEnergetique(*x)).reset_index()
dfChartEmission2SensJoursOuvres = dfChartEmission2Sens.loc[(dfChartEmission2Sens.indicateur == 'emission_bruit') & (~dfChartEmission2Sens.jour_sort.isin((108, 109, 110)))
                    & (dfChartEmission2Sens.jour_semaine.isin(range(5)))]
dfChartEmission2SensSamedi = dfChartEmission2Sens.loc[(dfChartEmission2Sens.indicateur == 'emission_bruit') & (~dfChartEmission2Sens.jour_sort.isin((108, 109, 110)))
                    & (dfChartEmission2Sens.jour_semaine == 5)]
dfChartEmission2SensDimanche = dfChartEmission2Sens.loc[(dfChartEmission2Sens.indicateur == 'emission_bruit') & (~dfChartEmission2Sens.jour_sort.isin((108, 109, 110)))
                    & (dfChartEmission2Sens.jour_semaine == 6)]

In [ ]:
# inclinaison rocade
dfInclinaisonS43 = pd.read_csv(r'C:\Users\martin.schoreisz\Box\Cerema\3E-Prod_Env_Risq\E6-Nuisances\E61-Acoustique\60-Etudes_Locales\2022-BruitRessentiBdxMet\4-Travaux_en_cours\donnees_produites\datas\inclinaison_rocade_S43.csv')
dfInclinaisonS44 = pd.read_csv(r'C:\Users\martin.schoreisz\Box\Cerema\3E-Prod_Env_Risq\E6-Nuisances\E61-Acoustique\60-Etudes_Locales\2022-BruitRessentiBdxMet\4-Travaux_en_cours\donnees_produites\datas\inclinaison_rocade_S44-S45.csv')
( alt.Chart(dfInclinaisonS43, title='Déclivité de la voie ; Rocade Sud', width=400, height=150).mark_line().encode(
    x=alt.X('sum:O', title='distance (m)', axis=alt.Axis(format=".2f", labelOverlap=True)),
    y=alt.Y('st_z:Q', title='altitude (m)')) | 
  alt.Chart(dfInclinaisonS44, title='Déclivité de la voie ; Rocade Nord', width=400, height=150).mark_line().encode(
    x=alt.X('sum:O', title='distance (m)', axis=alt.Axis(format=".2f", labelOverlap=True)),
    y=alt.Y('st_z:Q', title='altitude (m)')))

In [ ]:
# graph emission avec params
graphTraficVitesseEmission2SensSepares(dfChartEmission, largeur=800, hauteur=200, jour=104)

In [ ]:
# Graph emission 2 sens
graphEmissionBruitSensSepares(dfChartEmission, largeur=400, hauteur=250, jour=104)

In [ ]:
# graph de l'emission 2 sens pour l'ensemble des journées
graphEmissionBruitTousJours(dfChartEmission2SensDimanche, "Émission de bruit 2 sens confondus ; Dimanche")

In [ ]:
# densité de répartition 
graphDensiteBruitSelonSelection(dfChartEmission2SensJoursOuvres, 
                                "Dispersion de l'émission de bruit 2 sens confondus ; jours ouvrés",
                                errorBandType='stdev')

### vérif de calcul des émission par calcl par voie

In [ ]:
# vérif des calculs en calculant l'émission par voie puis en sommant
df6MinParSens = recupTraficEtVitesse6MinParSens(7, ['voie lente', 'voie médiane', 'voie rapide'])
dfNbVLPL6min = recupVlPl6min(7, sens=None, voie=['voie lente', 'voie médiane', 'voie rapide'])
dfVitesse = recupVitesseTV6min(7, sens=None, voie=['voie lente', 'voie médiane', 'voie rapide'])

In [ ]:
# correction des vitesses du dico
dfVitesse.loc[((dfVitesse.id_instru_site == 7) & (dfVitesse.sens == 'sens exter') & (dfVitesse.voie == 'voie lente')) &
                  (dfVitesse.date_heure.dt.strftime("%Y-%m-%d").isin(['2022-03-28', '2022-04-14', '2022-04-15', '2022-03-29'])), 'valeur'
             ] = dfVitesse.loc[((dfVitesse.id_instru_site == 7) & (dfVitesse.sens == 'sens exter') & (dfVitesse.voie == 'voie médiane')) &
                  (dfVitesse.date_heure.dt.strftime("%Y-%m-%d").isin(['2022-03-28', '2022-04-14', '2022-04-15', '2022-03-29']))
             ].valeur
dfVitesse.loc[((dfVitesse.id_instru_site == 7) & (dfVitesse.sens == 'sens inter') & (dfVitesse.voie == 'voie médiane')) &
                  (dfVitesse.date_heure.dt.strftime("%Y-%m-%d").isin(['2022-04-16', '2022-04-17', '2022-04-18'])), 'valeur'
             ] = dfVitesse.loc[((dfVitesse.id_instru_site == 7) & (dfVitesse.sens == 'sens exter') & (dfVitesse.voie == 'voie lente')) &
                  (dfVitesse.date_heure.dt.strftime("%Y-%m-%d").isin(['2022-04-16', '2022-04-17', '2022-04-18']))
             ].valeur

In [ ]:
# correction des vitesses à 0
dfVitesse.loc[((dfVitesse.id_instru_site == 7) & (dfVitesse.sens == 'sens exter') & (dfVitesse.voie == 'voie lente')) &
              (dfVitesse.valeur == 0), 'valeur'] = dfVitesse.loc[(dfVitesse.date_heure.isin(dfVitesse.loc[((dfVitesse.id_instru_site == 7) & (dfVitesse.sens == 'sens exter') & (dfVitesse.voie == 'voie rapide')) &
              (dfVitesse.valeur == 0)].date_heure.tolist()) ) & (dfVitesse.id_instru_site == 7) & (dfVitesse.sens == 'sens exter') & (dfVitesse.voie == 'voie médiane')
                                                              ].valeur
dfVitesse.loc[((dfVitesse.id_instru_site == 7) & (dfVitesse.sens == 'sens exter') & (dfVitesse.voie == 'voie médiane')) &
              (dfVitesse.valeur == 0), 'valeur'] = dfVitesse.loc[(dfVitesse.date_heure.isin(dfVitesse.loc[((dfVitesse.id_instru_site == 7) & (dfVitesse.sens == 'sens exter') & (dfVitesse.voie == 'voie rapide')) &
              (dfVitesse.valeur == 0)].date_heure.tolist()) ) & (dfVitesse.id_instru_site == 7) & (dfVitesse.sens == 'sens exter') & (dfVitesse.voie == 'voie lente')
                                                              ].valeur
dfVitesse.loc[((dfVitesse.id_instru_site == 7) & (dfVitesse.sens == 'sens exter') & (dfVitesse.voie == 'voie rapide')) &
              (dfVitesse.valeur == 0), 'valeur'] = dfVitesse.loc[(dfVitesse.date_heure.isin(dfVitesse.loc[((dfVitesse.id_instru_site == 7) & (dfVitesse.sens == 'sens exter') & (dfVitesse.voie == 'voie rapide')) &
              (dfVitesse.valeur == 0)].date_heure.tolist()) ) & (dfVitesse.id_instru_site == 7) & (dfVitesse.sens == 'sens exter') & (dfVitesse.voie == 'voie médiane')
                                                              ].valeur
dfVitesse.loc[((dfVitesse.id_instru_site == 7) & (dfVitesse.sens == 'sens inter') & (dfVitesse.voie == 'voie lente')) &
              (dfVitesse.valeur == 0), 'valeur'] = dfVitesse.loc[(dfVitesse.date_heure.isin(dfVitesse.loc[((dfVitesse.id_instru_site == 7) & (dfVitesse.sens == 'sens exter') & (dfVitesse.voie == 'voie rapide')) &
              (dfVitesse.valeur == 0)].date_heure.tolist()) ) & (dfVitesse.id_instru_site == 7) & (dfVitesse.sens == 'sens exter') & (dfVitesse.voie == 'voie médiane')
                                                              ].valeur
dfVitesse.loc[((dfVitesse.id_instru_site == 7) & (dfVitesse.sens == 'sens inter') & (dfVitesse.voie == 'voie médiane')) &
              (dfVitesse.valeur == 0), 'valeur'] = dfVitesse.loc[(dfVitesse.date_heure.isin(dfVitesse.loc[((dfVitesse.id_instru_site == 7) & (dfVitesse.sens == 'sens exter') & (dfVitesse.voie == 'voie rapide')) &
              (dfVitesse.valeur == 0)].date_heure.tolist()) ) & (dfVitesse.id_instru_site == 7) & (dfVitesse.sens == 'sens exter') & (dfVitesse.voie == 'voie lente')
                                                              ].valeur
dfVitesse.loc[((dfVitesse.id_instru_site == 7) & (dfVitesse.sens == 'sens inter') & (dfVitesse.voie == 'voie rapide')) &
              (dfVitesse.valeur == 0), 'valeur'] = dfVitesse.loc[(dfVitesse.date_heure.isin(dfVitesse.loc[((dfVitesse.id_instru_site == 7) & (dfVitesse.sens == 'sens exter') & (dfVitesse.voie == 'voie rapide')) &
              (dfVitesse.valeur == 0)].date_heure.tolist()) ) & (dfVitesse.id_instru_site == 7) & (dfVitesse.sens == 'sens exter') & (dfVitesse.voie == 'voie médiane')
                                                              ].valeur

In [ ]:
# verifs
dfVitesse.loc[((dfVitesse.id_instru_site == 7) & (dfVitesse.sens == 'sens inter') & (dfVitesse.voie == 'voie rapide')) &
              (dfVitesse.valeur == 0)]

In [ ]:
# calcul emission par voie
dfParamsEmission = dfNbVLPL6min.pivot(index=['date_heure', 'id_instru_site', 'jour', 'voie', 'sens'], columns='indicateur', values='valeur'
                   ).reset_index().merge(dfVitesse, on = ['date_heure', 'id_instru_site', 'voie', 'sens']
                                        ).rename(columns={'valeur': 'vitesseTV'}).drop(['id', 'indicateur', 'period_agreg'], axis=1, errors='ignore')
dfParamsEmission['declivite'] = dfParamsEmission.apply(lambda x: -3 if x.sens == 'sens inter' else 3, axis=1)
dfParamsEmission['age_rvt'] = dfParamsEmission.apply(lambda x: 6 if x.sens == 'sens inter' else 5, axis=1)
dfParamsEmission['emission_bruit'] = dfParamsEmission.apply(
    lambda x : Route(x.VL, x.PL, x.vitesseTV, x.vitesseTV, 'r3', x.age_rvt, 's', x.declivite, ignoreErreurVts=True).lwm, axis=1)
dfNivEmissionVoie = dfParamsEmission.pivot(index=['date_heure', 'jour', 'sens'], columns='voie', values='emission_bruit').reset_index()
dfNivEmissionVoie['emission_bruit'] = dfNivEmissionVoie.apply(lambda x: sommeEnergetique(x['voie lente'], x['voie médiane'], x['voie rapide']), axis=1)

In [ ]:
# verif : peu de différence
jour = 92
heure = 17
dfChartEmission.loc[(dfChartEmission.date_heure.dt.dayofyear == jour) & (dfChartEmission.date_heure.dt.hour == heure) & 
                     (dfChartEmission.indicateur == 'emission_bruit')].merge(
dfNivEmissionVoie.loc[(dfNivEmissionVoie.date_heure.dt.dayofyear == jour) & (dfNivEmissionVoie.date_heure.dt.hour == heure)],
on=['date_heure', 'sens'], suffixes=('_old', '_new'))

# ANALYSE CROISÉE TRAFICS BRUIT MÉTÉO

In [ ]:
# partie Trafic
# récupération des données 6 minutes de trafic (un peu long donc passé en comm)
df6MinParSens = recupTraficEtVitesse6MinParSens(7, ['section courante',])
dfEmissionTheorique = calculEmissionTheorique(df6MinParSens, 'sens inter', -3, 3, 5, 6, 'r3', 's')
# partie bruit
df6MinBruit = recupDonneesAgregees(4, '6 min').rename(columns={'leq_a': 'valeur'})
# partie météo
# meteo
dfMeteoBase = recupDonneesMeteoBase()
meteo = DonneesMeteo(dfMeteoBase, 1, 3, 18, '2022-03-21 13:00:00', 3)
angleEmmeteurRecepteur1, angleEmmeteurRecepteur2 = 90, 135
dfMeteo = meteo.propagationSourceRecepteurRiverain(meteo.dfAngleGradient, angleEmmeteurRecepteur1, angleEmmeteurRecepteur2)
dfBruitTraficMeteo, dfMeteo = fusionnerDfSources(dfEmissionTheorique, dfMeteo, df6MinBruit)

In [ ]:
# params et data
joursBruitHeteroGene = ([84, 96, 101], "Comparaison de jours avec niveaux de bruit mesurés fort, moyen et faible")
joursBruitFaible = ([89, 95, 96], "Comparaison de jours avec niveaux de bruit mesurés faible")
joursBruitFort = ([80, 101, 102])
joursBruitMoyen = ([82, 84, 92], )
jourMeteoFavRiverain = ([90, 99, 88, 89], "Comparaison de jours avec météo favorable au riverain")
jourMeteoDefavRiverain = ([81, 101, 102], "Comparaison de jours avec météo défavorable au riverain")
Samedi = ([85, 92, 99, 106], "Comparaison des Samedis") 
dfBruitTraficMeteo = pd.concat([df6MinBruit, dfChartEmission2Sens, dfMeteoChart])
dfBruitTraficMeteo.indicateur.replace(
    {'bruit': 'Mesure de bruit', 'emission_bruit': 'Émission de la route', 'grad_moy': 'Force de propagation du son',
    'temp_haut': 'Température'}, inplace=True)
jourGraph = joursBruitFort
# chart
graphCroiseBruitMeteoTrafic(dfBruitTraficMeteo, dfMeteo, joursBruitFaible[1], joursBruitFaible[0], domainBruit=(45, 90))

In [ ]:
graphCroiseBruitMeteoTrafic(dfBruitTraficMeteo, dfMeteo, Samedi[1], Samedi[0], domainBruit=(45, 90))

In [ ]:
# Corrélation
# préparation des données
dfCorrelation = creerCorrelation(dfBruitTraficMeteo)

In [ ]:
# corrélations
dfCorrelations = pd.concat([dfCorrelation.loc[~dfCorrelation.date_heure.dt.dayofyear.isin((108, 109, 110))].corr().assign(cas="tous jours"), 
                            dfCorrelation.loc[(dfCorrelation.date_heure.dt.dayofweek.isin(range(5)))
                                              & (~dfCorrelation.date_heure.dt.dayofyear.isin((108, 109, 110)))].corr().assign(
                                cas="jours ouvrés"),
                            dfCorrelation.loc[(dfCorrelation.date_heure.dt.dayofweek.isin(range(5)))],
                            dfCorrelation.loc[(dfCorrelation.date_heure.dt.dayofweek == 5)].corr().assign(cas="samedi"),
                            dfCorrelation.loc[(dfCorrelation.date_heure.dt.dayofweek == 6)].corr().assign(cas="dimanche")])

In [ ]:
dfChartCorrelation = dfCorrelations.loc['Mesure de bruit'].reset_index(
    drop=True).reset_index().melt(id_vars='cas', value_vars=
                                  ['Force de propagation du son', 'Émission de la route'], var_name='Paramètre', value_name='Corrélation')

In [ ]:
sortCas=["tous jours", ["tous jours", "sans grand vent"], ["jours ouvrés", "sans grand vent"], "samedi", "dimanche"]
alt.Chart(dfChartCorrelation.replace({'Force de propagation du son': 'Force de_propagation_du son', 
                                      'Émission de la route': 'Émission_de la route'}, regex=True)).mark_bar().encode(
    x=alt.X('Paramètre', title=None, axis=alt.Axis(labelAngle=45, labels=False)), 
    y=alt.Y('Corrélation', scale=alt.Scale(domain=(0, 1))),
    color=alt.Color('Paramètre', legend=alt.Legend(title=None, labelExpr="split(datum.value, '_')")),
    column=alt.Column('cas', spacing=50, sort=[0], title=["Corrélation entre le bruit mesuré, la force de propagation", "et l'émission de la route"]))